In [412]:
from __future__ import division, print_function, unicode_literals
import csv
from multiprocessing import Pool
from nupic.frameworks.opf.model_factory import ModelFactory
import datetime
import model_cpu
import model_mem
import model_disk
import net_params
from multiprocessing import Process
from nupic.algorithms import anomaly_likelihood
import shutil
import os
import time
import requests
import subprocess
from subprocess import call
import numpy as np
import tensorflow as tf


In [96]:
anomalyLikelihoodHelper = anomaly_likelihood.AnomalyLikelihood()


In [97]:
def reset_graph(seed=42):
    tf.reset_default_graph()
    tf.set_random_seed(seed)
    np.random.seed(seed)

In [413]:
def save_fig(fig_id, tight_layout=True):
    path = os.path.join(PROJECT_ROOT_DIR, "images", CHAPTER_ID, fig_id + ".png")
    print("Saving figure", fig_id)
    if tight_layout:
        plt.tight_layout()
    plt.savefig(path, format='png', dpi=300)

In [98]:
DATE_FORMAT = "%m/%d/%y %H:%M"
finalUtilityCpu=0.0 
SECONDS_PER_STEP= 15
adaptresult = {'metric': ' ', 'value':0, 'cost':0}
adaptoutcome = {'metric': ' ', 'value':0, 'cost':0, 'msg':''}
results=0
resultsA= []
prometheus='192.168.99.100'

In [263]:
def get_cpu_observation():
    model_cpu_model = ModelFactory.create(model_cpu.MODEL_PARAMS)
    model_cpu_model.enableInference({"predictedField": "cpu"})
    response = requests.get('http://admin:admin@'+prometheus+':9090/api/v1/query?query=sum(irate(node_cpu%7Bmode%3D%22idle%22%7D%5B30s%5D)%20*%20on(instance)%20group_left(node_name)%20node_meta%7Bnode_id%3D~%22.%2B%22%7D)%20*%20100%20%2F%20count(node_cpu%7Bmode%3D%22user%22%7D%20*%20on(instance)%20group_left(node_name)%20node_meta%7Bnode_id%3D~%22.%2B%22%7D)%20&start=1538182792&end=1538182852&step=30', timeout=5)
    results = response.json()
    cpuData = results['data']['result'] 
    if len(cpuData) > 0:
        cpuValue = cpuData[0]['value']
        timestamp = datetime.datetime.fromtimestamp(float(cpuValue[0])).strftime('%m/%d/%y %H:%M') 
        cpu = 100 - float(cpuValue[1])
       
        result = model_cpu_model.run({"cpu": cpu})
        prediction = result.inferences["multiStepBestPredictions"][1]
        anomalyScore = result.inferences['anomalyScore']
        anomalyLikelihood = anomalyLikelihoodHelper.anomalyProbability(cpu, anomalyScore, timestamp)
        utility_cpu = np.dot(anomalyLikelihood, cpu)
        print 'time: ', timestamp, ' cpu Usage: ',cpu , 'utility_cpu: ', utility_cpu
        cpu_axis=[cpu, prediction, anomalyScore, anomalyLikelihood, utility_cpu]
       
    
    cpu_axis=[cpu, prediction, anomalyScore, anomalyLikelihood, utility_cpu]
    return np.array(cpu_axis) 

In [266]:
#np.dot(f[:,0], f[:,2])/np.sum(f[:,2])

2.310343767925508

1.177143323678068

In [270]:
def get_mem_observation():
    model_mem_model = ModelFactory.create(model_mem.MODEL_PARAMS)
    model_mem_model.enableInference({"predictedField": "mem"})
    response = requests.get('http://admin:admin@'+prometheus+':9090/api/v1/query?query=sum((node_memory_MemAvailable%20%2F%20node_memory_MemTotal)%20*%20on(instance)%20group_left(node_name)%20node_meta%7Bnode_id%3D~%22.%2B%22%7D%20*%20100)%20%2F%20count(node_meta%20*%20on(instance)%20group_left(node_name)%20node_meta%7Bnode_id%3D~%22.%2B%22%7D)&start=1538181656&end=1538182556&step=30', timeout=5)
    results = response.json()
    memData = results['data']['result']
    if len(memData) > 0:
        memValue = memData[0]['value']
        timestamp = datetime.datetime.fromtimestamp(float(memValue[0])).strftime('%m/%d/%y %H:%M')
        mem = 100 - float(memValue[1])
        print 'time: ', timestamp, ' mem Usage: ',mem 
        result = model_mem_model.run({"mem": mem})
        prediction = result.inferences["multiStepBestPredictions"][1]
        anomalyScore = result.inferences['anomalyScore']
        anomalyLikelihood = anomalyLikelihoodHelper.anomalyProbability(mem, anomalyScore, timestamp)
        utility_mem = np.dot(anomalyLikelihood, mem)

       
    
    mem_axis=[mem, prediction, anomalyScore, anomalyLikelihood, utility_mem]
    return np.array(mem_axis) 

In [271]:
get_mem_observation()

time:  10/22/18 00:21  mem Usage:  43.9912985511


array([43.99129855, 43.99129855,  1.        ,  0.5       , 21.99564928])

In [272]:
def get_disk_observation():
    model_disk_model = ModelFactory.create(model_disk.MODEL_PARAMS)
    model_disk_model.enableInference({"predictedField": "disk"})
    response = requests.get('http://admin:admin@'+prometheus+':9090/api/v1/query?query=sum((node_filesystem_free%7Bmountpoint%3D%22%2F%22%7D%20%2F%20node_filesystem_size%7Bmountpoint%3D%22%2F%22%7D)%20*%20on(instance)%20group_left(node_name)%20node_meta%7Bnode_id%3D~%22.%2B%22%7D%20*%20100)%20%2F%20count(node_meta%20*%20on(instance)%20group_left(node_name)%20node_meta%7Bnode_id%3D~%22.%2B%22%7D)&start=1538181830&end=1538182730&step=30', timeout=5)
    results = response.json()
    diskData = results['data']['result'] 
    if len(diskData) > 0:
        diskValue = diskData[0]['value']
        timestamp = datetime.datetime.fromtimestamp(float(diskValue[0])).strftime('%m/%d/%y %H:%M')
        disk = 100 - float(diskValue[1])
        print 'time: ', timestamp,' disk Usage: ',disk 
        result = model_disk_model.run({"disk": disk})
        prediction = result.inferences["multiStepBestPredictions"][1]
        anomalyScore = result.inferences['anomalyScore']
        anomalyLikelihood = anomalyLikelihoodHelper.anomalyProbability(disk, anomalyScore, timestamp)
        utility_disk = np.dot(anomalyLikelihood, disk)

    disk_axis=[disk, prediction, anomalyScore, anomalyLikelihood,utility_disk]
    return np.array(disk_axis)

In [273]:
get_disk_observation()

time:  10/22/18 00:21  disk Usage:  17.2442298472


array([17.24422985, 17.24422985,  1.        ,  0.5       ,  8.62211492])

In [274]:
def get_net_observation():
    model_net = ModelFactory.create(net_params.MODEL_PARAMS)
    model_net.enableInference({"predictedField": "bytes_sent"})
    response = requests.get('http://admin:admin@'+prometheus+':9090/api/v1/query?query=sum(rate(container_network_receive_bytes_total%7Bcontainer_label_com_docker_swarm_node_id%3D~".%2B"%7D%5B30s%5D))%20by%20(container_label_com_docker_swarm_service_name)&start=1540150261&end=1540151161&step=30', timeout=5)
    results = response.json()
    diskData = results['data']['result'] 
    if len(diskData) > 0:
        diskValue = diskData[0]['value']
        timestamp = datetime.datetime.fromtimestamp(float(diskValue[0])).strftime('%m/%d/%y %H:%M')
        net = float(diskValue[1])
        print 'time: ', timestamp,' net bytes_sent: ',net 
        result = model_net.run({"bytes_sent": net})
        prediction = result.inferences["multiStepBestPredictions"][1]
        anomalyScore = result.inferences['anomalyScore']
        anomalyLikelihood = anomalyLikelihoodHelper.anomalyProbability(net, anomalyScore, timestamp)
        utility_net = np.dot(anomalyLikelihood, net)
    next_axis=[net, prediction, anomalyScore, anomalyLikelihood,utility_net]
    return np.array(next_axis)

In [275]:
get_net_observation()

time:  10/22/18 00:22  net bytes_sent:  0.0


array([0. , 0. , 1. , 0.5, 0. ])

In [276]:
def get_observation():
    disk_axis =  get_disk_observation()
    mem_axis = get_mem_observation()
    cpu_axis = get_cpu_observation()
    net_axis = get_net_observation()
    obs =np.vstack((cpu_axis,mem_axis, disk_axis, net_axis) )
    return obs 

In [301]:
l=[]
for i in range(10):
    a = get_observation()
    l.append(a)
    
f1= np.array(l)
    

time:  10/22/18 00:38  disk Usage:  17.2452065942
time:  10/22/18 00:38  mem Usage:  43.8102833226
time:  10/22/18 00:38  cpu Usage:  2.29071379363 utility_cpu:  1.1453568968140004
time:  10/22/18 00:38  net bytes_sent:  61.6
time:  10/22/18 00:38  disk Usage:  17.2452065942
time:  10/22/18 00:38  mem Usage:  43.8063599385
time:  10/22/18 00:38  cpu Usage:  2.29071379363 utility_cpu:  1.1453568968140004
time:  10/22/18 00:38  net bytes_sent:  163.811215301
time:  10/22/18 00:38  disk Usage:  17.2452228288
time:  10/22/18 00:38  mem Usage:  43.8065718191
time:  10/22/18 00:38  cpu Usage:  4.54648163132 utility_cpu:  2.2732408156605572
time:  10/22/18 00:38  net bytes_sent:  262.385810495
time:  10/22/18 00:38  disk Usage:  17.2452228288
time:  10/22/18 00:38  mem Usage:  43.8065718191
time:  10/22/18 00:38  cpu Usage:  4.54648163132 utility_cpu:  2.2732408156605572
time:  10/22/18 00:38  net bytes_sent:  68.4
time:  10/22/18 00:38  disk Usage:  17.2452228288
time:  10/22/18 00:38  mem U

In [300]:
np.dot(f[:,0], f[:,2])/np.sum(f[:,2])

2.31082257251623

In [277]:
obs = get_observation()
obs

time:  10/22/18 00:22  disk Usage:  17.2442635923
time:  10/22/18 00:22  mem Usage:  43.9992119811
time:  10/22/18 00:22  cpu Usage:  3.56211484934 utility_cpu:  1.7810574246678499
time:  10/22/18 00:22  net bytes_sent:  47.5968268782


array([[ 3.56211485,  3.56211485,  1.        ,  0.5       ,  1.78105742],
       [43.99921198, 43.99921198,  1.        ,  0.5       , 21.99960599],
       [17.24426359, 17.24426359,  1.        ,  0.5       ,  8.6221318 ],
       [47.59682688, 47.59682688,  1.        ,  0.5       , 23.79841344]])

In [318]:
l=[]
for i in range(10):
    a = get_cpu_observation()
    l.append(a)
    
f= np.array(l)
    

time:  10/22/18 00:49  cpu Usage:  2.45182869447 utility_cpu:  1.2259143472349194
time:  10/22/18 00:49  cpu Usage:  2.45182869447 utility_cpu:  1.2259143472349194
time:  10/22/18 00:49  cpu Usage:  2.45182869447 utility_cpu:  1.2259143472349194
time:  10/22/18 00:49  cpu Usage:  2.45182869447 utility_cpu:  1.2259143472349194
time:  10/22/18 00:49  cpu Usage:  2.46516202781 utility_cpu:  1.2325810139029443
time:  10/22/18 00:49  cpu Usage:  2.46516202781 utility_cpu:  1.2325810139029443
time:  10/22/18 00:49  cpu Usage:  2.46516202781 utility_cpu:  1.2325810139029443
time:  10/22/18 00:49  cpu Usage:  2.46516202781 utility_cpu:  1.2325810139029443
time:  10/22/18 00:49  cpu Usage:  2.46516202781 utility_cpu:  1.2325810139029443
time:  10/22/18 00:49  cpu Usage:  2.46516202781 utility_cpu:  1.2325810139029443


In [299]:
f.shape

(10, 5)

f1.shape

obs =np.vstack((cpu_axis,mem_axis, disk_axis, net_axis) )

In [311]:
#obs =np.vstack((cpu_axis,mem_axis, disk_axis, net_axis) )

net_fitnes = np.dot(f1[:,3, 0], f1[:,3,2])/np.sum(f1[:,3,2])
net_fitnes

mem_fitnes = np.dot(f1[:,1, 0], f1[:,1,2])/np.sum(f1[:,1,2])
mem_fitnes

cpu_fitnes = np.dot(f1[:,0, 0], f1[:,0,2])/np.sum(f1[:,0,2])
cpu_fitnes

disk_fitnes = np.dot(f1[:,2, 0], f1[:,2,2])/np.sum(f1[:,2,2])
disk_fitnes

94.69899179835048

In [316]:
f1.max(axis=1)

array([[  2.29071379,  43.81028332,  17.24520659,  61.6       ],
       [  2.29071379,  43.80635994,  17.24520659, 163.8112153 ],
       [  4.54648163,  43.80657182,  17.24522283, 262.3858105 ],
       [  4.54648163,  43.80657182,  17.24522283,  68.4       ],
       [  4.54648163,  43.80657182,  17.24522283,   1.        ],
       [  4.57053141,  43.80657182,  17.24522283,   1.        ],
       [  4.57053141,  43.80637565,  17.24522283,   1.        ],
       [  4.57053141,  43.80637565,  17.24522283, 262.3858105 ],
       [  4.57053141,  43.80637565,  17.24522283,   1.        ],
       [  4.57053141,  43.80637565,  17.24522283, 128.40708169]])

In [324]:
f1.shape[2]

5

In [180]:
n_inputs = obs.shape[0]
n_inputs

4

In [176]:
n_hidden = 10 

In [434]:
def discount_rewards(rewards, discount_rate):
    discounted_rewards = np.zeros(len(rewards))
    cumulative_rewards = 0
    for step in reversed(range(len(rewards))):
        cumulative_rewards = rewards[step] + cumulative_rewards * discount_rate
        discounted_rewards[step] = cumulative_rewards
    return discounted_rewards

def discount_and_normalize_rewards(all_rewards, discount_rate):
    all_discounted_rewards = [discount_rewards(rewards, discount_rate) for rewards in all_rewards]
    flat_rewards = np.concatenate(all_discounted_rewards)
    reward_mean = flat_rewards.mean()
    reward_std = flat_rewards.std()
    return [(discounted_rewards - reward_mean)/reward_std for discounted_rewards in all_discounted_rewards]

Set of possible States:  S= {s0, s1, s2, s3, s4}
Initial State: S0
Set of possible Actions: {a0, a1, a2, a3, a4,  a5}
Transition Model:T(s, a, s')
Reward Function = AnomalyLikelhood 

Let’s suppose we are programming the agent of the Microservice. Based on the CPU level we give a different reward at each time step. The rewards for the two terminal states remain the same (adapted=+1, Failed=-1). The obstacle at (2,2) is not a valid state and therefore there is no reward associated to it. Given these assumptions we can have four different cases:
1. R(S) <= -1.6284 High Anomaly Likelhood 
2. -0.4278 <= R(s) <= -0.085 quite high Anomaly Score 
3. -0.0221 <= R(s) <= 0 Slightly high Anomaly Score 
4. R(s) >=0  fully  converged low Anomaly Score 

The previous section terminated with a question: how can the agent choose the best policy? To give an answer to this question I will present the Bellman equation. 

\begin{equation*}
U_{h} = R(s_0) + \gamma R(s_1) + \gamma^{2} R(s_2) + ... + \gamma^{n} R(s_n)
\end{equation*}

The next step is to calculate the product between the utility and the transition probability, then sum up the value for each action.

\begin{equation*}
\pi^{*}(s) = \underset{a}{\text{ argmax }} \sum_{s^{'}}^{} T(s,a,s^{'}) U(s^{'})
\end{equation*}

\begin{equation*}
U(s_{11}) = -0.04 + 1.0 \times 0.7456 = 0.7056
\end{equation*}

## Possible actions
Scale Service Down = -1 S1

Stay in State S0 = 0 S0

Scale Service Up = 1 S2

Remove Node = 2 S3

Keep Node = 3 S0 

Add Node = 4 S4

In [320]:
current_state = get_observation()
current_state.max(axis=0)

time:  10/22/18 00:49  disk Usage:  17.2458915809
time:  10/22/18 00:49  mem Usage:  43.7406439344
time:  10/22/18 00:49  cpu Usage:  2.26584277464 utility_cpu:  1.1329213873210477
time:  10/22/18 00:49  net bytes_sent:  110.760445415


array([110.76044541, 110.76044541,   1.        ,   0.5       ,
        55.38022271])

In [177]:
possible_actions = [-1, 0, 1, 2, 3, 4]    

In [359]:
current_state = get_observation()
current_state

time:  10/22/18 01:22  disk Usage:  17.2478235057
time:  10/22/18 01:22  mem Usage:  43.7895309152
time:  10/22/18 01:22  cpu Usage:  3.34774405151 utility_cpu:  1.6738720257539157
time:  10/22/18 01:22  net bytes_sent:  111.034297725


array([[  3.34774405,   3.34774405,   1.        ,   0.5       ,
          1.67387203],
       [ 43.78953092,  43.78953092,   1.        ,   0.5       ,
         21.89476546],
       [ 17.24782351,  17.24782351,   1.        ,   0.5       ,
          8.62391175],
       [111.03429773, 111.03429773,   1.        ,   0.5       ,
         55.51714886]])

In [444]:
obs =np.vstack((cpu_axis,mem_axis, disk_axis, net_axis) )

net_fitnes = np.dot(f1[:,3, 0], f1[:,3,2])/np.sum(f1[:,3,2])
net_fitnes

mem_fitnes = np.dot(f1[:,1, 0], f1[:,1,2])/np.sum(f1[:,1,2])
mem_fitnes

cpu_fitnes = np.dot(f1[:,0, 0], f1[:,0,2])/np.sum(f1[:,0,2])
cpu_fitnes

disk_fitnes = np.dot(f1[:,2, 0], f1[:,2,2])/np.sum(f1[:,2,2])
disk_fitnes

NameError: name 'cpu_axis' is not defined

In [ ]:
def get_rate_of_changes(past_state, current_state):
    current_state = get_observation()
    cpu  = current_state[0, 0]
    mem  = current_state[1,0]
    disk   = current_state[2,0]  
    net =  current_state[3, 0]
    return cpu, mem, disk, net 
     

#uc= (anomalyLikelihood * cpu + prediction * anomalyLikelihood )/(anomalyLikelihood + anomalyLikelihood) 
      #calculate equ 1 in paper 
      sumOfUtilityFitness= sumOfUtilityFitness + (float(mem) * float(anomalyLikelihood))
      sumOfUtilityFitnessPredicted= sumOfUtilityFitnessPredicted + (float(prediction) * float(anomalyLikelihood))
      sumOfWeaight = sumOfWeaight + float(anomalyLikelihood)
      sumOfscore = sumOfscore + float(anomalyScore)

      #calculate equ 3 in paper 
  

      #calculate equ 4 in paper 
      Ucurr = (float(mem) * float(anomalyLikelihood))  
      diffChange = (Ucurr - Uprev)
      Uprev = Ucurr
      writer1.writerow([timestamp, mem, prediction, anomalyScore, anomalyLikelihood, sumOfUtilityFitness, sumOfUtilityFitnessPredicted, sumOfscore, sumOfWeaight, Uprev , diffChange] )
      
      try:
        time.sleep(2)
      except:
        pass
   fileHandle1.close()
   print 'sumOfWeaight: ', sumOfWeaight, 'sumOfUtilityFitness: ', sumOfUtilityFitness, 'sumOfUtilityFitnessPredicted: ', sumOfUtilityFitnessPredicted, 'diffChange: ', diffChange 
   result_output = 'mem_adapt.csv'
   utilityOfCpu=0.0
   with open(result_output, "rb") as result_input:
    csv_reader = csv.reader(result_input)
    csv_reader.next()
    for row in csv_reader:
      anomalyLikelihood = float(row[3])
      utilityOfmem= utilityOfmem + (anomalyLikelihood * sumOfUtilityFitness)/sumOfWeaight * diffChange
      utilityOfmemPredicted= utilityOfmemPredicted + (anomalyLikelihood * sumOfUtilityFitnessPredicted)/sumOfWeaight * diffChange
    cost = 0 
    if diffChange > 0:
      cost = round((utilityOfmem - utilityOfmemPredicted) * (sumOfWeaight * sumOfscore)/(diffChange * 5.34),0)
    print 'utilityOfMem: ', utilityOfmem, 'cost: ', cost
    adaptresult['metric'] = 'utilityOfMem'
    adaptresult['value'] = utilityOfmem
    adaptresult['cost'] = cost

In [442]:
past_state = get_observation()
current_state= get_observation()
change = past_state - current_state   

time:  10/22/18 13:46  disk Usage:  17.1324565371
time:  10/22/18 13:46  mem Usage:  44.5812188399
time:  10/22/18 13:46  cpu Usage:  2.44912101067 utility_cpu:  1.224560505337088
time:  10/22/18 13:46  net bytes_sent:  7253.38220593
time:  10/22/18 13:46  disk Usage:  17.1324565371
time:  10/22/18 13:46  mem Usage:  44.5812188399
time:  10/22/18 13:46  cpu Usage:  2.44912101067 utility_cpu:  1.224560505337088
time:  10/22/18 13:46  net bytes_sent:  258.070971185


In [443]:
change

array([[   0.        ,    0.        ,    0.        ,    0.        ,
           0.        ],
       [   0.        ,    0.        ,    0.        ,    0.        ,
           0.        ],
       [   0.        ,    0.        ,    0.        ,    0.        ,
           0.        ],
       [6995.31123475, 6995.31123475,    0.        ,    0.        ,
        3497.65561737]])

In [441]:
result = change.sum(axis=0)
result

array([149.86063383, 149.86063383,   0.        ,   0.        ,
        74.93031692])

In [403]:
def get_current_stat():
    current_state = get_observation()
    cpu_fitnes  = np.dot(current_state[0, 0], current_state[0,3])/np.sum(current_state[0,3])
    mem_fitnes  = np.dot(current_state[1,0], current_state[1,3])/np.sum(current_state[1,3])
    disk_fitnes  = np.dot(current_state[2,0],current_state[2,3])/np.sum(current_state[2,3])
    net_fitnes  = np.dot(current_state[3, 0],current_state[3,3])/np.sum(current_state[3,3])
    sum_utility =  cpu_fitnes+ mem_fitnes + disk_fitnes+ net_fitnes 
    return sum_utility

In [448]:
current_state = get_observation()
cpu_fitnes  = np.dot(current_state[0, 0] - current_state[0,1], current_state[0,3])/np.sum(current_state[0,3])
cpu_fitnes

time:  10/22/18 14:00  disk Usage:  17.1381400212
time:  10/22/18 14:00  mem Usage:  44.6215594366
time:  10/22/18 14:00  cpu Usage:  2.59868252095 utility_cpu:  1.2993412604735681
time:  10/22/18 14:00  net bytes_sent:  0.0


0.0

In [445]:
past_stat = get_current_stat()
current_state = get_current_stat()
print (past_state, current_state)


time:  10/22/18 13:58  disk Usage:  17.1331752688
time:  10/22/18 13:58  mem Usage:  44.5220116556
time:  10/22/18 13:58  cpu Usage:  2.25874867132 utility_cpu:  1.1293743356588806
time:  10/22/18 13:58  net bytes_sent:  68.4091212162
time:  10/22/18 13:58  disk Usage:  17.1331752688
time:  10/22/18 13:58  mem Usage:  44.5220116556
time:  10/22/18 13:58  cpu Usage:  2.25874867132 utility_cpu:  1.1293743356588806
time:  10/22/18 13:58  net bytes_sent:  61.6082144286
[[2.44912101e+00 2.44912101e+00 1.00000000e+00 5.00000000e-01
  1.22456051e+00]
 [4.45812188e+01 4.45812188e+01 1.00000000e+00 5.00000000e-01
  2.22906094e+01]
 [1.71324565e+01 1.71324565e+01 1.00000000e+00 5.00000000e-01
  8.56622827e+00]
 [7.25338221e+03 7.25338221e+03 1.00000000e+00 5.00000000e-01
  3.62669110e+03]] 125.52215002429313


In [419]:
def adaptation_step(action):
    
    past_stat = get_current_stat()
    cpu0, mem0, disk0, net0 =get_rate_of_changes()
    if action == -1:
            print("Scale Down Move to State S1")
            #Reward = max of utility fitness 
            current_state = get_current_stat()
            reward= current_state - past_stat
            cpu1, mem1, disk1, net1 =get_rate_of_changes()
            cpu_rate = cpu1 - cpu0/100
            mem_rate = mem1- mem0/100
            disk_rate = disk1 - disk0/100
            net_rate = net1 - net0/100
            done= False 
            info = "Scale Down Move to State S1"
    elif action == 0: 
        print("Stay in State S0")
        current_state = get_current_stat()
        reward= current_state - past_stat

        done= True 
        info = "Stay in State S0"
    elif action == 1: 
        print("Scale Service UP S2")
        current_state = get_current_stat()
        reward= current_state - past_stat
        done= False 
        info = "Stay in State S0"
    elif action == 2: 
        print("Remove Node S3")
        current_state = get_current_stat()
        reward= current_state - past_stat
        done= False
        info = "Remove Node S3"
    elif action == 3: 
        print("Mantain Cluster State S0")
        current_state = get_current_stat()
        reward= current_state - past_stat
        done= False
        info = "Mantain Cluster State S0"
    elif action == 4: 
        print("Add Node S4")
        current_state = get_current_stat()
        reward= current_state - past_stat
        done= False
        info = "Add Node S4"
    else: 
        print ("action not defined")
        current_state = get_current_stat()
        reward= current_state - past_stat
        info = "action not defined"
    
    state = get_observation()
     
    return np.array(state), reward, done, info
        

## Deep Q-Learning


In [420]:
tf.reset_default_graph()

# 1. Specify the network architecture
n_inputs = 200 # == 24
n_hidden = 4
n_outputs = len(possible_actions) # == 625
initializer = tf.variance_scaling_initializer()


In [421]:
# 2. Build the neural network
X = tf.placeholder(tf.float32, shape=[None, n_inputs])
hidden = tf.layers.dense(X, n_hidden, activation= tf.nn.softmax ,
                         kernel_initializer=initializer)
logits = tf.layers.dense(hidden, n_outputs,
                         kernel_initializer=initializer)
outputs = tf.nn.softmax(logits)


In [422]:
# 3. Select a random action based on the estimated probabilities

action_index = tf.squeeze(tf.multinomial(logits, num_samples=1), axis=-1)
action_index


<tf.Tensor 'Squeeze:0' shape=(?,) dtype=int64>

In [423]:
# 4. Training
learning_rate = 0.01

y = tf.one_hot(action_index, depth=len(possible_actions))
print(y)
cross_entropy = tf.nn.softmax_cross_entropy_with_logits_v2(labels=y, logits=logits)
optimizer = tf.train.AdamOptimizer(learning_rate)
grads_and_vars = optimizer.compute_gradients(cross_entropy)
gradients = [grad for grad, variable in grads_and_vars]
gradient_placeholders = []
grads_and_vars_feed = []
for grad, variable in grads_and_vars:
    gradient_placeholder = tf.placeholder(tf.float32, shape=grad.get_shape())
    gradient_placeholders.append(gradient_placeholder)
    grads_and_vars_feed.append((gradient_placeholder, variable))
training_op = optimizer.apply_gradients(grads_and_vars_feed)

init = tf.global_variables_initializer()
saver = tf.train.Saver()

Tensor("one_hot:0", shape=(?, 6), dtype=float32)


In [424]:
def run_bipedal_walker(model_path=None, n_max_steps = 2000):
    with tf.Session() as sess:
        if model_path is None:
            init.run()
        else:
            saver.restore(sess, model_path)
        obs = get_observation()
        for step in range(n_max_steps):
            action_index_val = action_index.eval(feed_dict={X: f1.reshape(1, n_inputs)})
            print(action_index_val)
            action = possible_actions[int(action_index_val)]
            #action = np.random.randint(0,5)
            print (action)
            obs, reward, done, info = adaptation_step(action)
            print ("obs: ",obs, \
                   "reward: ", reward, \
                   "done: ", done, \
                   "info: ", info)
            if done:
                break
      

In [425]:
#run_bipedal_walker()

In [435]:
n_games_per_update = 10
n_max_steps = 1000
n_iterations = 1000
save_iterations = 10
discount_rate = 0.95

with tf.Session() as sess:
    init.run()
    for iteration in range(n_iterations):
        print("\rIteration: {}/{}".format(iteration + 1, n_iterations), end="")
        all_rewards = []
        all_gradients = []
        for game in range(n_games_per_update):
            current_rewards = []
            current_gradients = []
            obs = get_observation()
            for step in range(n_max_steps):
                action_index_val, gradients_val = sess.run([action_index, gradients],
                                                           feed_dict={X: f1.reshape(1, n_inputs)})
                action = possible_actions[int(action_index_val)]
                obs, reward, done, info = adaptation_step(action)
                current_rewards.append(reward)
                current_gradients.append(gradients_val)
                if done:
                    break
            all_rewards.append(current_rewards)
            all_gradients.append(current_gradients)

        all_rewards = discount_and_normalize_rewards(all_rewards, discount_rate=discount_rate)
        feed_dict = {}
        for var_index, gradient_placeholder in enumerate(gradient_placeholders):
            mean_gradients = np.mean([reward * all_gradients[game_index][step][var_index]
                                      for game_index, rewards in enumerate(all_rewards)
                                          for step, reward in enumerate(rewards)], axis=0)
            feed_dict[gradient_placeholder] = mean_gradients
        sess.run(training_op, feed_dict=feed_dict)
        if iteration % save_iterations == 0:
            saver.save(sess, "./my_bipedal_walker_pg.ckpt")

Iteration: 1/1000time:  10/22/18 02:13  disk Usage:  17.2605523298
time:  10/22/18 02:13  mem Usage:  43.9802004084
time:  10/22/18 02:13  cpu Usage:  2.26669851042 utility_cpu:  1.1333492552086923
time:  10/22/18 02:13  net bytes_sent:  41.0420414418
time:  10/22/18 02:13  disk Usage:  17.2605523298
time:  10/22/18 02:13  mem Usage:  43.9802004084
time:  10/22/18 02:13  cpu Usage:  2.26669851042 utility_cpu:  1.1333492552086923
time:  10/22/18 02:13  net bytes_sent:  7266.5733893
Mantain Cluster State S0
time:  10/22/18 02:13  disk Usage:  17.2605523298
time:  10/22/18 02:13  mem Usage:  43.9802004084
time:  10/22/18 02:13  cpu Usage:  2.26669851042 utility_cpu:  1.1333492552086923
time:  10/22/18 02:13  net bytes_sent:  97.4147637407
time:  10/22/18 02:13  disk Usage:  17.2605523298
time:  10/22/18 02:13  mem Usage:  43.9802004084
time:  10/22/18 02:13  cpu Usage:  2.26669851042 utility_cpu:  1.1333492552086923
time:  10/22/18 02:13  net bytes_sent:  0.0
time:  10/22/18 02:13  disk U

time:  10/22/18 02:14  cpu Usage:  22.0520752966 utility_cpu:  11.026037648321292
time:  10/22/18 02:14  net bytes_sent:  0.0
time:  10/22/18 02:14  disk Usage:  17.2605860749
time:  10/22/18 02:14  mem Usage:  43.9763820667
time:  10/22/18 02:14  cpu Usage:  22.0520752966 utility_cpu:  11.026037648321292
time:  10/22/18 02:14  net bytes_sent:  137.40916686
Scale Down Move to State S1
time:  10/22/18 02:14  disk Usage:  17.2605860749
time:  10/22/18 02:14  mem Usage:  43.9763820667
time:  10/22/18 02:14  cpu Usage:  22.0520752966 utility_cpu:  11.026037648321292
time:  10/22/18 02:14  net bytes_sent:  181.3395715
time:  10/22/18 02:14  disk Usage:  17.2605860749
time:  10/22/18 02:14  mem Usage:  43.9763820667
time:  10/22/18 02:14  cpu Usage:  22.0520752966 utility_cpu:  11.026037648321292
time:  10/22/18 02:14  net bytes_sent:  260.681197094
time:  10/22/18 02:14  disk Usage:  17.2605860749
time:  10/22/18 02:14  mem Usage:  43.9737337823
time:  10/22/18 02:14  cpu Usage:  22.0254086

time:  10/22/18 02:14  mem Usage:  44.1035086802
time:  10/22/18 02:14  cpu Usage:  21.881314579 utility_cpu:  10.940657289513936
time:  10/22/18 02:14  net bytes_sent:  0.0
time:  10/22/18 02:14  disk Usage:  17.2606144853
time:  10/22/18 02:14  mem Usage:  44.1035086802
time:  10/22/18 02:14  cpu Usage:  21.881314579 utility_cpu:  10.940657289513936
time:  10/22/18 02:14  net bytes_sent:  0.0
time:  10/22/18 02:14  disk Usage:  17.2606144853
time:  10/22/18 02:14  mem Usage:  44.1035086802
time:  10/22/18 02:14  cpu Usage:  21.881314579 utility_cpu:  10.940657289513936
time:  10/22/18 02:14  net bytes_sent:  0.0
Remove Node S3
time:  10/22/18 02:14  disk Usage:  17.2606144853
time:  10/22/18 02:14  mem Usage:  44.1057646261
time:  10/22/18 02:14  cpu Usage:  21.881314579 utility_cpu:  10.940657289513936
time:  10/22/18 02:14  net bytes_sent:  110.810643075
time:  10/22/18 02:14  disk Usage:  17.2606144853
time:  10/22/18 02:14  mem Usage:  44.1057646261
time:  10/22/18 02:14  cpu Usa

time:  10/22/18 02:15  mem Usage:  43.9959316521
time:  10/22/18 02:15  cpu Usage:  22.0323407051 utility_cpu:  11.0161703525552
time:  10/22/18 02:15  net bytes_sent:  110.797933708
time:  10/22/18 02:15  disk Usage:  17.2605820163
time:  10/22/18 02:15  mem Usage:  43.9959316521
time:  10/22/18 02:15  cpu Usage:  22.0323407051 utility_cpu:  11.0161703525552
time:  10/22/18 02:15  net bytes_sent:  110.797933708
time:  10/22/18 02:15  disk Usage:  17.2605820163
time:  10/22/18 02:15  mem Usage:  43.9959316521
time:  10/22/18 02:15  cpu Usage:  21.9790073718 utility_cpu:  10.98950368589037
time:  10/22/18 02:15  net bytes_sent:  163.796160571
time:  10/22/18 02:15  disk Usage:  17.2605820163
time:  10/22/18 02:15  mem Usage:  43.9953431444
time:  10/22/18 02:15  cpu Usage:  21.9790073718 utility_cpu:  10.98950368589037
time:  10/22/18 02:15  net bytes_sent:  0.0
Mantain Cluster State S0
time:  10/22/18 02:15  disk Usage:  17.2605820163
time:  10/22/18 02:15  mem Usage:  43.9953431444
ti

time:  10/22/18 02:15  net bytes_sent:  10345.4278663
Mantain Cluster State S0
time:  10/22/18 02:15  disk Usage:  17.2606063681
time:  10/22/18 02:15  mem Usage:  44.0204680655
time:  10/22/18 02:15  cpu Usage:  21.7973292547 utility_cpu:  10.898664627353334
time:  10/22/18 02:15  net bytes_sent:  61.628760088
time:  10/22/18 02:15  disk Usage:  17.2606063681
time:  10/22/18 02:15  mem Usage:  44.0212527424
time:  10/22/18 02:15  cpu Usage:  21.8119762782 utility_cpu:  10.905988139118143
time:  10/22/18 02:15  net bytes_sent:  0.0
time:  10/22/18 02:15  disk Usage:  17.2606063681
time:  10/22/18 02:15  mem Usage:  44.0212527424
time:  10/22/18 02:15  cpu Usage:  21.8119762782 utility_cpu:  10.905988139118143
time:  10/22/18 02:15  net bytes_sent:  10345.4278663
Add Node S4
time:  10/22/18 02:15  disk Usage:  17.2606063681
time:  10/22/18 02:15  mem Usage:  44.0212527424
time:  10/22/18 02:15  cpu Usage:  21.8119762782 utility_cpu:  10.905988139118143
time:  10/22/18 02:15  net bytes_s

...

time:  10/22/18 06:06  disk Usage:  17.2978044268
time:  10/22/18 06:06  mem Usage:  44.9405511742
time:  10/22/18 06:06  cpu Usage:  21.9188951036 utility_cpu:  10.959447551818677
time:  10/22/18 06:06  net bytes_sent:  61.5753698521
time:  10/22/18 06:06  disk Usage:  17.2978044268
time:  10/22/18 06:06  mem Usage:  44.9405511742
time:  10/22/18 06:06  cpu Usage:  21.9188951036 utility_cpu:  10.959447551818677
time:  10/22/18 06:06  net bytes_sent:  320.6
time:  10/22/18 06:06  disk Usage:  17.2978044268
time:  10/22/18 06:06  mem Usage:  44.9405511742
time:  10/22/18 06:06  cpu Usage:  21.9188951036 utility_cpu:  10.959447551818677
time:  10/22/18 06:06  net bytes_sent:  110.818910076
Mantain Cluster State S0
time:  10/22/18 06:06  disk Usage:  17.2978044268
time:  10/22/18 06:06  mem Usage:  44.9405511742
time:  10/22/18 06:06  cpu Usage:  21.9188951036 utility_cpu:  10.959447551818677
time:  10/22/18 06:06  net bytes_sent:  0.0
time:  10/22/18 06:06  disk Usage:  17.2978044268
tim

time:  10/22/18 06:06  net bytes_sent:  101.812989186
Mantain Cluster State S0
time:  10/22/18 06:06  disk Usage:  17.2978287786
time:  10/22/18 06:06  mem Usage:  44.4461727227
time:  10/22/18 06:06  cpu Usage:  21.8626737053 utility_cpu:  10.931336852628178
time:  10/22/18 06:06  net bytes_sent:  61.5835777126
time:  10/22/18 06:06  disk Usage:  17.2978287786
time:  10/22/18 06:06  mem Usage:  44.4461727227
time:  10/22/18 06:06  cpu Usage:  21.8626737053 utility_cpu:  10.931336852628178
time:  10/22/18 06:06  net bytes_sent:  10.0006667111
time:  10/22/18 06:06  disk Usage:  17.2978287786
time:  10/22/18 06:06  mem Usage:  44.4461727227
time:  10/22/18 06:06  cpu Usage:  21.8626737053 utility_cpu:  10.931336852628178
time:  10/22/18 06:06  net bytes_sent:  10.0006667111
Add Node S4
time:  10/22/18 06:06  disk Usage:  17.2978287786
time:  10/22/18 06:06  mem Usage:  44.4461727227
time:  10/22/18 06:06  cpu Usage:  21.8626737053 utility_cpu:  10.931336852628178
time:  10/22/18 06:06  

time:  10/22/18 06:07  net bytes_sent:  119.450739901
time:  10/22/18 06:07  disk Usage:  17.298672974
time:  10/22/18 06:07  mem Usage:  44.9108822669
time:  10/22/18 06:07  cpu Usage:  40.5706709316 utility_cpu:  20.285335465801484
time:  10/22/18 06:07  net bytes_sent:  184.127103468
Mantain Cluster State S0
time:  10/22/18 06:07  disk Usage:  17.298672974
time:  10/22/18 06:07  mem Usage:  44.9108822669
time:  10/22/18 06:07  cpu Usage:  40.5706709316 utility_cpu:  20.285335465801484
time:  10/22/18 06:07  net bytes_sent:  124.00206708
time:  10/22/18 06:07  disk Usage:  17.298672974
time:  10/22/18 06:07  mem Usage:  44.9108822669
time:  10/22/18 06:07  cpu Usage:  40.5706709316 utility_cpu:  20.285335465801484
time:  10/22/18 06:07  net bytes_sent:  0.0
time:  10/22/18 06:07  disk Usage:  17.298672974
time:  10/22/18 06:07  mem Usage:  44.9108822669
time:  10/22/18 06:07  cpu Usage:  40.5706709316 utility_cpu:  20.285335465801484
time:  10/22/18 06:07  net bytes_sent:  0.0
Add No

time:  10/22/18 06:07  cpu Usage:  21.9809604746 utility_cpu:  10.990480237303949
time:  10/22/18 06:07  net bytes_sent:  132.793802656
Add Node S4
time:  10/22/18 06:07  disk Usage:  17.0774653557
time:  10/22/18 06:07  mem Usage:  44.3816128587
time:  10/22/18 06:07  cpu Usage:  21.9809604746 utility_cpu:  10.990480237303949
time:  10/22/18 06:07  net bytes_sent:  132.793802656
time:  10/22/18 06:07  disk Usage:  17.0774653557
time:  10/22/18 06:07  mem Usage:  44.3876941041
time:  10/22/18 06:07  cpu Usage:  21.9542938079 utility_cpu:  10.977146903967899
time:  10/22/18 06:07  net bytes_sent:  110.793509225
time:  10/22/18 06:07  disk Usage:  17.0774653557
time:  10/22/18 06:07  mem Usage:  44.3876941041
time:  10/22/18 06:07  cpu Usage:  21.9542938079 utility_cpu:  10.977146903967899
time:  10/22/18 06:07  net bytes_sent:  0.0
Remove Node S3
time:  10/22/18 06:07  disk Usage:  17.0774653557
time:  10/22/18 06:07  mem Usage:  44.3876941041
time:  10/22/18 06:07  cpu Usage:  21.95429

RuntimeError: Python exception raised. Unable to extract info

In [449]:
run_bipedal_walker("./my_bipedal_walker_pg.ckpt")

INFO:tensorflow:Restoring parameters from ./my_bipedal_walker_pg.ckpt
time:  10/22/18 15:17  disk Usage:  17.1460976473
time:  10/22/18 15:17  mem Usage:  44.6052430566
time:  10/22/18 15:17  cpu Usage:  2.30092171403 utility_cpu:  1.150460857012618
time:  10/22/18 15:17  net bytes_sent:  110.760550331
[5]
4
time:  10/22/18 15:17  disk Usage:  17.1460976473
time:  10/22/18 15:17  mem Usage:  44.6052430566
time:  10/22/18 15:17  cpu Usage:  2.27450837776 utility_cpu:  1.1372541888820393
time:  10/22/18 15:17  net bytes_sent:  163.710724461
Add Node S4
time:  10/22/18 15:17  disk Usage:  17.1460976473
time:  10/22/18 15:17  mem Usage:  44.6078913409
time:  10/22/18 15:17  cpu Usage:  2.27450837776 utility_cpu:  1.1372541888820393
time:  10/22/18 15:17  net bytes_sent:  178.475906806
time:  10/22/18 15:17  disk Usage:  17.1460976473
time:  10/22/18 15:17  mem Usage:  44.6078913409
time:  10/22/18 15:17  cpu Usage:  2.27450837776 utility_cpu:  1.1372541888820393
time:  10/22/18 15:17  net 